In [1]:
import open3d.ml as _ml3d
import open3d as o3d
import open3d.ml.torch as ml3d  # just switch to open3d.ml.tf for tf usage
import os

import warnings
warnings.filterwarnings("ignore")

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
import torch
print(torch.cuda.is_available())

True


In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [4]:
cfg_file = "configs/kpconv_semantic3d_OPTIMIZEDFORTRAINING.yml"
cfg = _ml3d.utils.Config.load_from_file(cfg_file)

In [5]:
device

device(type='cuda')

In [6]:
dataset = ml3d.datasets.Semantic3D(dataset_path='/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled', use_cache=True)

#dataset = CustomSemantic3D(dataset_path='/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_downsampled', use_cache=True)

In [7]:
dataset.get_split_list("train")

array(['/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/bildstein_station1_xyz_intensity_rgb.txt',
       '/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/bildstein_station5_xyz_intensity_rgb.txt',
       '/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/domfountain_station1_xyz_intensity_rgb.txt',
       '/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/domfountain_station2_xyz_intensity_rgb.txt',
       '/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/domfountain_station3_xyz_intensity_rgb.txt',
       '/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/neugasse_station1_xyz_intensity_rgb.txt',
       '/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/sg27_station1_intensity_rgb.txt',
       '/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/sg27_station4_intensity_rgb.txt',
       '/mnt/d/Krishna/Research/Datasets/Semantic3D/semantic_dsampled/sg27_station5_intensity_rgb.txt',
     

In [8]:
model = ml3d.models.KPFCNN(**cfg.model)

In [9]:
pipeline = ml3d.pipelines.SemanticSegmentation(model=model, dataset=dataset, device="gpu", **cfg.pipeline)

In [10]:
import os

ckpt_folder = "./logs/"
os.makedirs(ckpt_folder, exist_ok=True)
ckpt_path = ckpt_folder + "kpconv_semantic3d.pth"

In [11]:
'''
ADDED ENTRIES

num_workers: 0
pin_memory: False

TO THE yml FILE IN UNDER THE PIPELINE SECTION FOR THE RuntimeError OCCURED DUE TO COMPUTE CONSTRAINTS
'''

'\nADDED ENTRIES\n\nnum_workers: 0\npin_memory: False\n\nTO THE yml FILE IN UNDER THE PIPELINE SECTION FOR THE RuntimeError OCCURED DUE TO COMPUTE CONSTRAINTS\n'

In [12]:
%%time

pipeline.run_train()

validation: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:15<00:00,  7.54s/it]


CPU times: user 5h 22min 10s, sys: 7h 39min 44s, total: 13h 1min 54s
Wall time: 4d 20h 19min 42s


### Inference

Testing directly on IIITB data

In [13]:
cfg_file_1 = "configs/kpconv_semantic3d_OPTIMIZEDFORTRAINING.yml"
cfg_1 = _ml3d.utils.Config.load_from_file(cfg_file_1)

cfg_1.dataset['dataset_path'] = "/mnt/d/Krishna/Research/Datasets/Semantic3D/"
dataset = ml3d.datasets.Semantic3D(cfg_1.dataset.pop('dataset_path', None), **cfg_1.dataset)
#pipeline = ml3d.pipelines.SemanticSegmentation(model, dataset=dataset, device="gpu", **cfg.pipeline)

# download the weights.
#ckpt_folder = "logs/KPFCNN_Semantic3D_torch/checkpoint/"
#os.makedirs(ckpt_folder, exist_ok=True)
#ckpt_path = ckpt_folder + "ckpt_05000.pth"

In [14]:
# load the parameters.
#pipeline.load_ckpt(ckpt_path=ckpt_path)

In [15]:
dataset.get_split_list("test")

array(['/mnt/d/Krishna/Research/Datasets/Semantic3D/IIIT_Base.txt'],
      dtype='<U57')

In [16]:
test_split = dataset.get_split("test")
dataTest = test_split.get_data(0)

In [17]:
result = pipeline.run_inference(dataTest)

test 0/1: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████| 1417791/1417791 [39:40<00:00, 398.98it/s]

In [18]:
print(result)

{'predict_labels': array([0, 0, 0, ..., 0, 0, 0]), 'predict_scores': array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float16)}


In [19]:
len(result['predict_labels'])

2275320

In [20]:
set(result['predict_labels'])

{0, 2, 4, 6}

In [21]:
newData = dataTest

In [22]:
newData['label'] = result['predict_labels']

In [23]:
import numpy as np

# Assuming newData is already defined as in your example

# Combine all data into a single array for writing to a text file
# Structure: x, y, z, r, g, b, label
data_to_write = np.hstack((
    newData['point'],                       # x, y, z coordinates
    newData['feat'][:, :3],                 # r, g, b colors
    newData['label'].reshape(-1, 1)         # label as a single column
))

# Save to a text file
np.savetxt("output_point_cloud_10000_new.txt", data_to_write, fmt='%.6f %.6f %.6f %.3f %.3f %.3f %d')

print("Point cloud data with labels saved to output_point_cloud.txt")

Point cloud data with labels saved to output_point_cloud.txt
